In [1]:
import faculty.datasets as datasets
import matplotlib.pyplot as plt
import nltk
import numpy as np
import pandas as pd
import spacy
%matplotlib inline


2023-02-28 17:01:01.735612: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/anaconda/envs/Python3/lib:
2023-02-28 17:01:01.735687: W tensorflow/stream_executor/cuda/cuda_driver.cc:269] failed call to cuInit: UNKNOWN ERROR (303)
2023-02-28 17:01:01.735713: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (cube-b2f6b542-b29a-4672-9ac9-c005bf019a65-844657fdc8-8rszg): /proc/driver/nvidia/version does not exist


In [3]:
df = pd.read_excel('/project/my-society/data/raw/plans.xlsx')
df_missing = df[df['text'].isna()]
df_dirty = df[df['text'].notna()]

In [19]:
import re
import unicodedata

def is_pua(c):
    return unicodedata.category(c) == 'Co'

def clean_plan(text):
    # take out all duplicated whitespace so each word separated by one space
    text = ' '.join(text.split())
    text = text.lower()
    #remove the private use characters
    text = "".join([char for char in text if not is_pua(char)])
    text = text.replace('_x000C_','')
    text = text.replace('xc','')
    # remove all non-alphanumeric
    text = re.sub("[^A-Za-z. ]",'',text)
    return text

In [20]:
df_clean = df_dirty
df_clean['text'] = df_dirty['text'].map(clean_plan)
test_corpus = df_clean['text']

/tmp/ipykernel_121572/1372362497.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean['text'] = df_dirty['text'].map(clean_plan)


In [22]:
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

def lemmatize(text):
    doc = nlp(text)
    # Turn it into tokens, ignoring the punctuation
    tokens = [token for token in doc if not token.is_punct]
    # Convert those tokens into lemmas, EXCEPT the pronouns, we'll keep those.
    lemmas = [token.lemma_ if token.pos_ != 'PRON' else token.orth_ for token in tokens]
    return lemmas

In [34]:
lemmatize(test_corpus[5])

['carbon',
 'neutral',
 'plan',
 'work',
 'towards',
 'the',
 'target',
 'december',
 ' ',
 'adur',
 'worthe',
 'council',
 'carbon',
 'neutral',
 'plan',
 'aecom',
 'quality',
 'information',
 'prepare',
 'by',
 'check',
 'by',
 'approve',
 'by',
 'sam',
 'shuttleworth',
 'matthew',
 'turner',
 'matthew',
 'turner',
 'principal',
 'consultant',
 'regional',
 'director',
 'regional',
 'director',
 'harper',
 'robertson',
 'consultant',
 'revision',
 'history',
 'revision',
 'revision',
 'date',
 'detail',
 'name',
 'position',
 'first',
 'draft',
 'matthew',
 'turner',
 'regional',
 'director',
 'first',
 'draft',
 'business',
 'travel',
 'add',
 'matthew',
 'turner',
 'regional',
 'director',
 'second',
 'draft',
 'matthew',
 'turner',
 'regional',
 'director',
 'final',
 'matthew',
 'turner',
 'regional',
 'director',
 'distribution',
 'list',
 'hard',
 'copy',
 'pdf',
 'require',
 'association',
 'company',
 'name',
 'na',
 'y',
 'adur',
 'worthe',
 'council',
 'prepare',
 'for',
 '

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction import text

my_stop_words = text.ENGLISH_STOP_WORDS
tfidf_vectorizer = TfidfVectorizer(use_idf=True,tokenizer=lemmatize, stop_words="english", max_features=200,ngram_range=(2,3))#hyperparameter to explore


tfidf_vectors = tfidf_vectorizer.fit_transform(df_clean['text'])

In [140]:
# print out your vectors in a nice way
features = tfidf_vectorizer.get_feature_names()
for i, row in enumerate(tfidf_vectors.toarray()):
    # print out your vectors in a nice way
    print(
        pd.DataFrame({"Terms": features, "Frq_id_freq": row}).to_string(index=False)
    )
    print("-" * 40)

/opt/anaconda/envs/Python3/lib/python3.9/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


                          Terms  Frq_id_freq
                        climate     0.000000
                 achieve carbon     0.000000
                    achieve net     0.000000
               achieve net zero     0.000000
                 action climate     0.000000
          action climate change     0.000000
                 action council     0.000000
                    action need     0.000000
                    action plan     0.036474
                  action reduce     0.000000
                  active travel     0.135074
                address climate     0.191173
                    adur worthe     0.000000
                    air quality     0.000000
               behaviour change     0.224511
                borough council     0.000000
                business travel     0.000000
                  carbon budget     0.069205
                 carbon dioxide     0.050763
                carbon emission     0.035034
                  carbon energy     0.000000
          

                          Terms  Frq_id_freq
                        climate          0.0
                 achieve carbon          0.0
                    achieve net          0.0
               achieve net zero          0.0
                 action climate          0.0
          action climate change          0.0
                 action council          0.0
                    action need          0.0
                    action plan          0.0
                  action reduce          0.0
                  active travel          0.0
                address climate          0.0
                    adur worthe          0.0
                    air quality          0.0
               behaviour change          0.0
                borough council          0.0
                business travel          0.0
                  carbon budget          0.0
                 carbon dioxide          0.0
                carbon emission          0.0
                  carbon energy          0.0
          

In [141]:
features = tfidf_vectorizer.get_feature_names()
features

/opt/anaconda/envs/Python3/lib/python3.9/site-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


['  climate',
 'achieve carbon',
 'achieve net',
 'achieve net zero',
 'action climate',
 'action climate change',
 'action council',
 'action need',
 'action plan',
 'action reduce',
 'active travel',
 'address climate',
 'adur worthe',
 'air quality',
 'behaviour change',
 'borough council',
 'business travel',
 'carbon budget',
 'carbon dioxide',
 'carbon emission',
 'carbon energy',
 'carbon footprint',
 'carbon management',
 'carbon management plan',
 'carbon neutral',
 'carbon neutrality',
 'carbon offset',
 'carbon reduction',
 'change act',
 'change action',
 'change action plan',
 'change climate',
 'change impact',
 'change need',
 'change strategy',
 'charge point',
 'city council',
 'city region',
 'clean air',
 'climate action',
 'climate action plan',
 'climate change',
 'climate change act',
 'climate change action',
 'climate change strategy',
 'climate ecological',
 'climate ecological emergency',
 'climate emergency',
 'climate emergency action',
 'climate emergency d

In [142]:
len(features)

200

In [271]:
# pip install -U sentence-transformers

In [144]:
import os
os.environ["HF_ENDPOINT"] = "https://huggingface.co"

from sentence_transformers import SentenceTransformer

model = SentenceTransformer("whaleloops/phrase-bert")

In [145]:
from scipy.spatial.distance import cdist

In [212]:
phrase_embs = model.encode(features) #returns np array shape (200,768)

dot_similarity = np.dot(phrase_embs,phrase_embs.T)
# np.fill_diagonal(dot_similarity,0)
cos_similarity = 1- cdist(phrase_embs,phrase_embs, 'cosine')
# np.fill_diagonal(cos_similarity,0)

In [223]:
dot_df =pd.DataFrame(
    dot_similarity,
    index=features,
    columns=features,
)

cos_df =pd.DataFrame(
    cos_similarity,
    index=features,
    columns=features,
)

In [303]:

data =cos_df.loc['achieve carbon'].sort_values(ascending=False).index.to_list()

h= pd.DataFrame(index=range(200),columns = cos_df.index.to_list())

for col in h.columns:
    h[col] = cos_df.loc[col].sort_values(ascending=False).index.to_list()

In [320]:

sim_words = h.transpose()
sim_words.to_csv('model1_similar_phrases.csv')




## Thoughts on baseline
- Produces too many overlapping phrases. e.g. council declare and council declare climate, strategy action and strategy action plan
- Produces opposite phrases. e.g long term and short term, private sector and public sector. People won't want to search for both
- Produces nonsense like protect enhance, action reduce